In [2]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [3]:
from jax import vmap, jit
import jax.numpy as jnp
from pathlib import Path
import numpy as np
from einops import rearrange
import jax
import matplotlib.pyplot as plt
import seaborn as sns
from hflow.misc.plot import scatter_movie, imshow_movie

In [4]:
import jax.random
from diffrax import diffeqsolve, ControlTerm, Euler, MultiTerm, ODETerm, SaveAt, VirtualBrownianTree, Heun, WeaklyDiagonalControlTerm
import random
from hflow.test.plot import get_hist


In [33]:
from hflow.data.vlasov import run_vlasov
from hflow.misc.misc import (gauss_quadrature_weights_points,
                             pts_array_from_space)
from hflow.train.sample import interplate_in_t
from hflow.data.utils import normalize


bs_t = 128
n_samples = 10_000
n_t = 1000
t0, t1 = 0, 30
t_eval = np.linspace(t0, t1, n_t)
mu = 1.7
sols = run_vlasov(n_samples, t_eval, mu, mode='two-stream')



t_train = t_eval / t_eval[-1]
t_train = t_train.reshape(-1, 1)
g_pts_01, quad_weights = gauss_quadrature_weights_points(
    bs_t, a=0.0, b=1.0)

start, end = jnp.asarray([0]), jnp.asarray([1.0])
g_pts_01 = jnp.concatenate([start, g_pts_01, end])

sols = rearrange(np.expand_dims(sols, 0), 'M T N D -> T M N D')
# interp
sols = interplate_in_t(sols, t_train, g_pts_01)
sols = rearrange(sols, 'T M N D -> (T M) N D')

t_train = g_pts_01.reshape(-1,1)
sols, d_shift, d_scale = normalize(
    sols, axis=(0, 1), return_stats=True, method='01')

In [28]:


H = get_hist(sols)
imshow_movie(H, title=mu)

In [34]:


H = get_hist(sols)
imshow_movie(H, title=mu)

In [16]:


H = get_hist(sols)
imshow_movie(H, title=mu)